# Accessibility Analysis using OpenRouteService

In [1]:
import folium
from folium import Map, Marker, FeatureGroup, LayerControl
from folium.plugins import MarkerCluster

from openrouteservice import client, geocode, directions, places #
from openrouteservice import * # client

#import numpy as np
import pandas as pd 
import time 

import fiona as fn
from shapely.geometry import shape, Polygon, mapping
from shapely.ops import cascaded_union

from pprint import pprint #

- create map
- input shapefile of districts
- input shapefile of health facilities

## Preprocessing

In [2]:
#api_key = '58d904a497c67e00015b45fc2a6b6872037d44119582ef40cdf264c4' # Provide your personal API key
api_key = '58d904a497c67e00015b45fca522cb32f97347829754df32f76a48bb'
clnt = client.Client(key=api_key)
map_outline = folium.Map(tiles='Stamen Toner', location=([-18.812718, 46.713867]), zoom_start=5)

# Shapefiles from https://data.humdata.org/dataset/madagascar-administrative-boundary-shapefiles-level-1-4 (05/07/2018)
district_original = []
district_simp = []
with fn.open('mdg_polbnda_adm2_Distritcts_BNGRC_OCHA.shp', 'r') as districts:
    for polygon in districts:
        district_original.append(polygon)
        # Create and simplify geometry
        geom = shape(polygon['geometry'])
        simp_geom = geom.simplify(0.0002, preserve_topology=False)
        simp_coord = mapping(simp_geom)
        folium.GeoJson(simp_coord).add_to(map_outline)
        district_simp.append(simp_coord)
        
print('There are {} districts.'.format(len(district_original)))        


cluster = MarkerCluster().add_to(map_outline) # To cluster hospitals

# Health facilities from https://data.humdata.org/dataset/madagascar-healthsites (05/07/2018)
facility = []
with fn.open('healthsites.shp', 'r') as facility_data:
    for poi in facility_data:
        folium.Marker(list(reversed(poi['geometry']['coordinates']))).add_to(cluster)
        facility.append(poi)
    
map_outline

There are 119 districts.


In [5]:
# population per district
# http://www.worldpop.org.uk/data/files/index.php?dataset=571&zip_title=Madagascar%20100m%20Population&action=group (05.07.2018)
# Data were modified: intersected with district borders in qgis
district_pop = [] #
district_plot_data = []
pop_count = [] #
df_district_data = []
with fn.open('district_pop_final.shp', 'r') as dist_pop_data:
    for polygon in dist_pop_data:
        district_pop.append(polygon)
        district_name = polygon['properties']['REGION_NAM']
        district_code = polygon['properties']['DIST_PCODE']
        district_pop_count = round(polygon['properties']['sum'])
        pop_count.append(polygon['properties']['sum'])
        district_plot_data += [[district_name, district_code, district_pop_count]]

        df_district_data.append({'District Code': district_code,
                                 'Population Count': district_pop_count})
        
df_district = pd.DataFrame(df_district_data) # Create Table out of data
#display(df_district)

total_pop = sum(pop_count)
print('Madagascar has a total population of {:.0f}.'.format(sum(pop_count)))

Madagascar has a total population of 27798005.


In [3]:
print('There are {} health facilities.'.format(len(facility))) ####

There are 121 health facilities.


## second part

- isochrone for 1 hour foot walk

In [3]:
# 1 hour Isochrones for foot walking and car driving
map_isochrones = folium.Map(tiles='Stamen Toner', location=([-18.812718, 46.713867]), zoom_start=5)

def style_function(color): # To style isochrones
    return lambda feature: dict(color=color)

iso_foot = []
iso_car = []
iso_car_error = [] #
for loc in facility:
    try:
        iso_params = {'locations': loc['geometry']['coordinates'],
                          'profile': 'foot-walking',
                          'range_type': 'time',
                          'segments': 3600, # 3600=1hour
                          'attributes': {'total_pop', 'area'}}
        iso_foot_request = clnt.isochrones(**iso_params)
        lon, lat = loc['geometry']['coordinates']
        #icon = folium.map.Icon(color='#fff3e6',
         #                           icon_color='red',
          #                          icon='hospital-symbol', # fetches font-awesome.io symbols
           #                         prefix='fa')
        #popup = "Meta Data: {}".format(iso_foot_request['features'][0]['properties']) ##
        #folium.map.Marker([lat, lon]).add_to(map_isochrones) #, icon=icon, popup=popup
        iso_foot.append(iso_foot_request)
        if len(iso_foot) % 39 == 0:
            time.sleep(60)
    except Exception as err:
        print(err)
        print(loc['geometry']['coordinates'])
        iso_car_error.append(loc['geometry']['coordinates']) #
        pass

500 ({'error': {'code': 3099, 'message': 'Unable to build an isochrone map.'}, 'info': {'engine': {'version': '4.5.0', 'build_date': '2018-06-12T17:36:31Z'}, 'timestamp': 1531929585343}})
(47.3285816, -14.8355601)
500 ({'error': {'code': 3099, 'message': 'Unable to build an isochrone map.'}, 'info': {'engine': {'version': '4.5.0', 'build_date': '2018-06-12T17:36:31Z'}, 'timestamp': 1531929646613}})
(45.8711619, -16.008446)


In [6]:
print('There are {} health facilities.'.format(len(iso_foot)))

There are 119 health facilities.


- 1 hour isochrone for car drive

In [7]:
# isochrones for car
iso_car = []
for loc in facility:
    try:
        iso_params = {'locations': loc['geometry']['coordinates'],
                          'profile': 'driving-car',
                          'range_type': 'time',
                          'segments': 3600, # 3600=1hour
                          'attributes': {'total_pop', 'area'}}
        iso_car_request = clnt.isochrones(**iso_params)
        iso_car.append(iso_car_request)
        if len(iso_car) % 39 == 0:
            time.sleep(60)
    except Exception as err:
        print(err)
        print(loc['geometry']['coordinates'])
        pass

('Connection aborted.', OSError("(104, 'ECONNRESET')",))
(47.5310067, -18.9082844)
500 ({'error': {'code': 3099, 'message': 'Unable to build an isochrone map.'}, 'info': {'engine': {'version': '4.5.0', 'build_date': '2018-06-13T06:21:46Z'}, 'timestamp': 1531929854840}})
(47.3285816, -14.8355601)
500 ({'error': {'code': 3099, 'message': 'Unable to build an isochrone map.'}, 'info': {'engine': {'version': '4.5.0', 'build_date': '2018-06-12T14:47:57Z'}, 'timestamp': 1531929855409}})
(49.8509648, -17.001741)


In [ ]:
# population per district with access

- union of isochrones

In [8]:
# union der isochrone -> ist egal zu welchem Krankenhaus die gehen
# car
iso_geom_car = []
for iso in iso_car:
    iso_geom_car.append(shape(iso['features'][0]['geometry']))

iso_union_car = cascaded_union(iso_geom_car)
union_coord_car = mapping(iso_union_car)

for l in union_coord_car['coordinates']:
    switched_coords = [[(y,x) for x,y in l[0]]]
    folium.features.PolygonMarker(switched_coords,
                            color='#ff751a',
                             fill_color='#ff751a',
                            fill_opacity=0.2,
                             weight=3).add_to(map_isochrones)


# foot
iso_geom_foot = []
for iso in iso_foot:
    iso_geom_foot.append(shape(iso['features'][0]['geometry']))
    
iso_union_foot = cascaded_union(iso_geom_foot)
union_coord_foot = mapping(iso_union_foot)

for l in union_coord_foot['coordinates']:
    switched_coords = [[(y,x) for x,y in l[0]]]
    folium.features.PolygonMarker(switched_coords,
                            color='#ffd699',
                             fill_color='#ffd699',
                            fill_opacity=0.2,
                             weight=3).add_to(map_isochrones)
    
map_isochrones

- export union isochrones to modify in qgis

In [71]:
# export and modifing in qgis -> population per union_isochrone
## car
# Define a polygon feature geometry with one attribute
schema_car = {'geometry': 'Polygon',
              'properties': {'id': 'int'}}
index_car = 0
# Write a new Shapefile
with fn.open('iso_union_car.shp', 'w', 'ESRI Shapefile', schema_car) as c:
    for poly in iso_union_car:
        index_car += 1 
        c.write({'geometry': mapping(poly),
                 'properties': {'id': index_car}})


## foot
# Define a polygon feature geometry with one attribute
schema_foot = {'geometry': 'Polygon',
               'properties': {'id': 'int'}}
index_foot = 0
# Write a new Shapefile
with fn.open('iso_union_foot.shp', 'w', 'ESRI Shapefile', schema_foot) as c:
    for poly in iso_union_foot:
        index_foot += 1 
        c.write({'geometry': mapping(poly),
                 'properties': {'id': index_foot}})

- import modified shapefile -> population per union isochrone and district

In [14]:
# import modified shapefiles
pop_mod_car = [] 
with fn.open('pop_dist_iso_car.shp', 'r') as pop_data_car:
    for car_data in pop_data_car:
        pop_mod_car.append(car_data)


pop_mod_food = []
with fn.open('pop_district_iso.shp', 'r') as pop_data_foot:
    for foot_data in pop_data_foot:
        pop_mod_food.append(foot_data)

print('There are {} districts with health facilities which are accessable by car and {} districts accessable by foot.'.format(len(pop_mod_car), len(pop_mod_food)))

There are 84 districts with health facilities which are accessable by car and 50 districts accessable by foot.


- population data as raster file
- intersected with district borders in qgis
- input new shapefile

## Analysis
- % of population with access to health facilities per district

In [15]:
# % of population with access to health facilities per district 

### car
#plot_data_car = []
df_carpop_data = []
df_car_data = []

for district in pop_mod_car:
    district_code = district['properties']['DIST_PCODE']
    district_name = district['properties']['DISTRICT_N']
    district_pop_access = round(district['properties']['ppd_sum']) # Population with access per district 

    for location in district_plot_data:
        if district_code == location[1]:
            pop_district = location[2]
            
            df_carpop_data.append({'District Code': district_code,
                                'Car: Pop. with access': district_pop_access,
                                  'Population per district': pop_district})
            
            df_car_data.append({'District Code': district_code,
                            'District Name': district_name})
            
df_carpop = pd.DataFrame(df_carpop_data)
df_carpop = df_carpop.groupby('District Code').mean() # umbennen?
df_carpop = df_carpop.groupby('District Code')['Car: Pop. with access', 'Population per district'].sum() # sum values if row are splitted

df_carpop['Car: Pop. with access [%]'] = round(df_carpop.loc[:,'Car: Pop. with access']/df_carpop.loc[:, 'Population per district']*100, 2)

df_carpop = pd.DataFrame(df_carpop)
df_car = pd.DataFrame(df_car_data)

df_car = df_car.drop_duplicates(keep='first') # drop first of double rows

df_car_plot = pd.merge(df_carpop, df_car, how='left', on='District Code') # Merge two tables


### foot
df_foot_data = []
    
for district in pop_mod_food:
    district_name = district['properties']['REGION_NAM']
    district_code = district['properties']['DIST_PCODE']
    district_pop_access = round(district['properties']['popnew_sum'])

    for location in district_plot_data:
        if district_code == location[1]: 
            per_access_foot = round(district_pop_access/location[2]*100, 2)
            
            df_foot_data.append({'District Code': district_code,
                                   'Foot: Pop. with access': district_pop_access,
                                    'Foot: Pop. with access [%]': per_access_foot})

df_foot = pd.DataFrame(df_foot_data)

In [ ]:
# District Names == Nan not 0

In [16]:
# merge tables

df_distcar = pd.merge(df_district, df_car_plot, how='left', on='District Code') # Merge Districts with Car values
df_total = pd.merge(df_distcar, df_foot, how='left', on='District Code') # Merge DataFrame with Foot values
df_total = df_total.fillna(0)
df_total = df_total[['District Code', 'District Name', 'Population Count', 'Foot: Pop. with access', 'Foot: Pop. with access [%]', 'Car: Pop. with access', 'Car: Pop. with access [%]']] # 
display(df_total)

District Code              District Name  Population Count  \
0     MDG11101001         1er Arrondissement            323165   
1     MDG11101002          2e Arrondissement            248922   
2     MDG11101003          3e Arrondissement            173950   
3     MDG11101004          4e Arrondissement            331633   
4     MDG11101005          5e Arrondissement            406466   
5     MDG11101006          6e Arrondissement            169175   
6        MDG11102    Antananarivo Avaradrano            461396   
7        MDG11103             Ambohidratrimo            507845   
8        MDG11104                   Ankazobe            192866   
9        MDG11106             Manjakandriana            259821   
10       MDG11107                 Anjozorobe            225434   
11       MDG11115                Andramasina            216513   
12       MDG11117  Antananarivo Atsimondrano            744751   
13       MDG12108                Antsirabe I            303506   
14       MDG12109                     Betafo            324196   
15       MDG12110                Ambatolampy            326014   
16       MDG12114                Antanifotsy            391913   
17       MDG12116                  Faratsiho            246010   
18       MDG12118               Antsirabe II            517156   
19       MDG12120                    Mandoto            186234   
20       MDG13105                Arivonimamo            388079   
21       MDG13112                Miarinarivo            306316   
22       MDG13113             Soavinandriana            238267   
23       MDG14111            Tsiroanomandidy            416071   
24       MDG14119                          0            166012   
25       MDG21201             Fianarantsoa I            242214   
26       MDG21205                  Ambalavao            266520   
27       MDG21208              Ambohimahasoa            273248   
28       MDG21219                          0            113745   
29       MDG21220                  Lalangina            215805   
..            ...                        ...               ...   
89       MDG51501                  Toliary-I            199441   
90       MDG51503                          0             58172   
91       MDG51504                          0            149126   
92       MDG51505                          0             83437   
93       MDG51506                          0            261321   
94       MDG51507             Ampanihy Ouest            394750   
95       MDG51512                          0            143915   
96       MDG51520                 Toliary-II            336370   
97       MDG51521                          0             49274   
98       MDG52513                          0            139182   
99       MDG52514                          0            140181   
100      MDG52516                          0            445014   
101      MDG52518                     Bekily            209675   
102      MDG53515                 Taolagnaro            346014   
103      MDG53517                          0            242873   
104      MDG53519           Amboasary-Atsimo            266105   
105      MDG54502                          0             95674   
106      MDG54508                          0            153324   
107      MDG54509                          0            180132   
108      MDG54510                          0            157985   
109      MDG54511                          0            166453   
110      MDG71713             Antsiranana II            134161   
111      MDG71715              Antsiranana I            146377   
112      MDG71717                          0            275083   
113      MDG71718                    Nosy-Be             92918   
114      MDG71719                          0            242362   
115      MDG72710                   Antalaha            294598   
116      MDG72711                    Sambava            387360   
117      MDG72712                     Andapa

In [ ]:
#### beispiel
map.geo_json(geo_path=state_geo, data=state_data,
             columns=['State', 'Unemployment'],
             key_on='feature.id',
             fill_color='YlGn', fill_opacity=0.7, line_opacity=0.2,
             legend_name='Unemployment Rate (%)')

m.choropleth(
    geo_str=open('us-states.json').read(),
    data=unemployment,
    columns=['State', 'Unemployment'],
    key_on='feature.id',
    fill_color='YlGn',
    )

In [ ]:
# map with map districts choropleth
map_choropleth = folium.Map(tiles='Stamen Toner', location=([-18.812718, 46.713867]), zoom_start=5)
perc_foot = df_total.loc[:,'Foot: Pop. with access [%]']

map_choropleth.choropleth(geo_data=perc_foot,
                            data=perc_foot,
                          fill_color='YlGn'
                         )
map_choropleth